## Setup

In [ ]:
# %% 🚀 SETUP
%load_ext autoreload
%autoreload 2

import sys
from pathlib import Path
sys.path.append(str(Path("../src").resolve()))   # <== cartella src

# ---- genera due DFA di test e compone ----
from dfa_generator import dfa_parity, dfa_contains, compose, simulate_samples
from pta_builder    import PTA

dfa1 = dfa_parity("a", 2)
dfa2 = dfa_contains("bb", {"a", "b"})
product = compose([dfa1, dfa2], "intersection")

S_pos, S_neg = simulate_samples(product,
                                max_len=10,
                                n_positive=200,
                                n_negative=200,
                                seed=42)

pta = PTA.build(S_pos, S_neg)
print("✅ PTA costruita:", pta)


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
✅ PTA costruita: <PTA: |Q|=236317, |Σ|=2>


## Reduction

In [10]:
# %% 🧩 CONSISTENT REDUCTION
from pathlib import Path, PurePosixPath
import importlib, reduction          # importa modulo appena patchato

importlib.reload(reduction)          # forza ricaricamento pulito

# usa SEMPRE l'alias sicuro
from reduction import reduce_pta     

reduced = reduce_pta(pta)
print("✅ DFA ridotto:", reduced)

Path("figs").mkdir(exist_ok=True)
Path("figs/dfa_reduced.dot").write_text(reduced.to_dot())
print("📝 DOT salvato in figs/dfa_reduced.dot")


✅ DFA ridotto: DFA(states={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216

## Verification

In [11]:
# %% ✔️ VERIFICA COERENZA
assert all(reduced.accepts(w)  for w in S_pos), "Errore: qualche S⁺ non accettato"
assert all(not reduced.accepts(w) for w in S_neg), "Errore: qualche S⁻ accettato"
print("🎉 Il DFA ridotto è coerente con S⁺ / S⁻")


🎉 Il DFA ridotto è coerente con S⁺ / S⁻


In [12]:
# %% ✔️ Verifica di coerenza DFA ridotto

errors_pos = [w for w in S_pos if not reduced.accepts(w)]
errors_neg = [w for w in S_neg if reduced.accepts(w)]

print(f"✔️ Accettati correttamente: {len(S_pos) - len(errors_pos)} / {len(S_pos)} in S⁺")
print(f"✔️ Rifiutati correttamente: {len(S_neg) - len(errors_neg)} / {len(S_neg)} in S⁻")

assert not errors_pos, f"❌ Alcune stringhe di S⁺ non sono accettate: {errors_pos[:3]}"
assert not errors_neg, f"❌ Alcune stringhe di S⁻ sono state accettate: {errors_neg[:3]}"

print("🎉 Il DFA ridotto è perfettamente coerente con i campioni S⁺ / S⁻")


✔️ Accettati correttamente: 500 / 500 in S⁺
✔️ Rifiutati correttamente: 500 / 500 in S⁻
🎉 Il DFA ridotto è perfettamente coerente con i campioni S⁺ / S⁻
